In [16]:
# Imports
import osmnx as ox
import networkx as nx
import pandas as pd
import geopandas as gpd
from shapely.geometry import LineString, Point, Polygon, MultiPolygon
import copy
import shapely
from shapely.ops import split

In [20]:
# Flag to generate network or use existing
GENERATE_NEW_NETWORK = False

In [21]:
# Network Setup
network_type = 'walk'
# custom filter for building walk network
cf = """
     ["area"!~"yes"]
     ["highway"]
     ["highway"!~"motor|proposed|construction|abandoned|platform|raceway"]
     ["foot"!~"no"]
     ["service"!~"private"]
     ["access"!~"private"]
     """

# bounding box (left, bottom, right, top) in lat/lon
bbox = -92.444115, 38.834019, -92.171516, 39.031239

travel_speed = 4.5  # walking speed in km/hour


In [22]:
if(GENERATE_NEW_NETWORK):
    # create network from bounding box using a custom filter
    graph = ox.graph_from_bbox(bbox, custom_filter=cf, network_type=network_type)

    # save graph as GPKG and GraphML
    ox.io.save_graph_geopackage(graph, filepath="data/network/columbia-walk-network.gpkg")
    ox.io.save_graphml(graph, filepath="data/network/columbia-walk-network.graphml")

In [30]:
# Load walk network
G = ox.io.load_graphml(filepath="data/network/columbia-walk-network.graphml")

# Project graph to UTM
G = ox.projection.project_graph(G)

# Load input data
grocery_stores = gpd.read_file("data/inputs/grocery_points.geojson")
health_points = gpd.read_file("data/inputs/health_points.geojson")
elementary_schools = gpd.read_file("data/inputs/elementary_school_points.geojson")
city_parks = gpd.read_file("data/inputs/parks_poly.geojson")

# reproject to the same crs as the graph
grocery_stores = grocery_stores.to_crs(G.graph['crs'])
health_points = health_points.to_crs(G.graph['crs'])
elementary_schools = elementary_schools.to_crs(G.graph['crs'])
city_parks = city_parks.to_crs(G.graph['crs'])

In [32]:
def find_closest_nodes(idx, row, layer_name):
    # Get nearest edge (returns a tuple: (u, v, key))
    nearest_edge = ox.distance.nearest_edges(G, X=row.geometry.x, Y=row.geometry.y)

    # Get the geometry of the nearest edge
    edge_data = G.get_edge_data(*nearest_edge)

    edge_geom = edge_data.get('geometry')

    # If edge has no geometry (some edges are just straight lines between nodes)
    if edge_geom is None:
        u = G.nodes[nearest_edge[0]]
        v = G.nodes[nearest_edge[1]]
        edge_geom = LineString([(u['x'], u['y']), (v['x'], v['y'])])

    origin_geom = row.geometry  # Ensure it's a shapely Point
    nearest_pt_on_edge = edge_geom.interpolate(edge_geom.project(origin_geom))

    # find nearest node
    nearest_node = ox.distance.nearest_nodes(G, X=origin_geom.x, Y=origin_geom.y)

    # Get the coordinates of the nearest node
    nearest_node_coords = (G.nodes[nearest_node]["x"], G.nodes[nearest_node]["y"])

    # nearest_points.append({
    #     'uid': row['uid'],
    #     'node_id': int(nearest_node),
    #     'geometry': Point(nearest_node_coords)
    # })

    # Measure the distance between the point and the nearest node
    distance_to_nearest_node = nearest_pt_on_edge.distance(Point(nearest_node_coords))

    # if distance is less than 0.5 meters
    if(distance_to_nearest_node < 0.5):
        print(f"Distance to nearest node within 0.5 meters, skipping (uid: {row['uid']}, {distance_to_nearest_node} meters)")
        
        nearest_points.append({
            'uid': row['uid'],
            'node_id': int(nearest_node),
            'layer_name': layer_name,
            'geometry': Point(nearest_node_coords)
        })
    else:
    # Append the geometry (Point), node_id, and uid as a dictionary
        nearest_points.append({
            'uid': row['uid'],
            'node_id': -1, # Denotes this as a newly created node, thus needs to be added to the network
            'layer_name': layer_name,
            'geometry': nearest_pt_on_edge
        })

    return nearest_points



nearest_points = []


# Find closest node to each grocery store
for idx, row in grocery_stores.iterrows():
    find_closest_nodes(idx, row, 'grocery_stores')

# Find closest node to each health point
for idx, row in health_points.iterrows():
    find_closest_nodes(idx, row, 'health_points')

# Find closest node to each elementary school
for idx, row in elementary_schools.iterrows():
    find_closest_nodes(idx, row, 'elementary_schools')
    
print(nearest_points)

# Create a GeoDataFrame from the list of features
gdf_nearest_points = gpd.GeoDataFrame(nearest_points)

# Assign graph CRS for reprojection to work correctly
gdf_nearest_points.set_crs(G.graph['crs'], inplace=True)

# Reproject to EPSG:4326 (WGS84 lat/lon)
gdf_nearest_points_projected = gdf_nearest_points.to_crs("EPSG:4326")
# Export to GeoJSON
gdf_nearest_points_projected.to_file("data/nearest_nodes.geojson", driver="GeoJSON")

Distance to nearest node within 0.5 meters, skipping (uid: 7, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 2, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 6, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 15, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 13, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 14, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 16, 0.0 meters)
Distance to nearest node within 0.5 meters, skipping (uid: 19, 0.0 meters)
[{'uid': 1, 'node_id': -1, 'layer_name': 'grocery_stores', 'geometry': <POINT (557770.652 4307184.786)>}, {'uid': 2, 'node_id': -1, 'layer_name': 'grocery_stores', 'geometry': <POINT (558576.482 4307409.481)>}, {'uid': 3, 'node_id': -1, 'layer_name': 'grocery_stores', 'geometry': <POINT (557601.769 4311461.242)>}, {'uid': 4, 'node_id': -1, 'layer_name': 'grocery_stores', 'geometry': <POINT (555574.69

In [ ]:
# Create new nodes on edges for routing (if nearest node to origin isn't within 0.5m of point on edge)

# -- Copy graph for safe editing
G_modified = G.copy()

# Copy geodataframe to prevent from having to regenerate each time
gdf_nearest_points_copy = copy.deepcopy(gdf_nearest_points)

# -- Track new nodes
new_node_ids = []

t_u = 0
t_v = 0

for idx, row in gdf_nearest_points_copy.iterrows():
    # if node_id has already been assigned, skip
    if row['node_id'] != -1:
        print(f"skipping node for uid: {row.uid}")
        continue
    
    snapped_point = row.geometry
    uid = row.uid

    # 1. Find nearest edge
    u, v, key = ox.distance.nearest_edges(G_modified, X=snapped_point.x, Y=snapped_point.y)

    edge_data = G_modified.get_edge_data(u, v, key)
    edge_geom = edge_data.get("geometry")

    if edge_geom is None:
        point_u = (G_modified.nodes[u]["x"], G_modified.nodes[u]["y"])
        point_v = (G_modified.nodes[v]["x"], G_modified.nodes[v]["y"])
        edge_geom = LineString([point_u, point_v])


    # use a small linestring to split
    splitter = LineString([
        (snapped_point.x - 0.001, snapped_point.y),
        (snapped_point.x + 0.001, snapped_point.y)
    ])

    split_lines = split(edge_geom, splitter)

    # If split fails, skip
    if len(split_lines.geoms) != 2:
        print(f"Warning: Could not split edge {u}-{v} cleanly at uid {uid}")
        continue

    # remove the original edge(s)
    G_modified.remove_edge(u, v, key)
    
    # check if reciprocal edge is in graph, if so remove as well
    if((v, u, key) in G_modified.edges()):
        G_modified.remove_edge(v, u, key)

    # create new node
    new_node_id = max(G_modified.nodes) + 1
    G_modified.add_node(new_node_id, x=snapped_point.x, y=snapped_point.y, street_count=2) # street count is 2 since we're bisecting the existing edge
    
    # set node_id for newly created node in dataframe
    gdf_nearest_points_copy.at[idx, 'node_id'] = new_node_id
    
    u_to_node = False
    node_to_v = False

    make_u_next = False
    make_v_next = False

    for i, segment in enumerate(split_lines.geoms):
        attrs = edge_data.copy()
        attrs["geometry"] = segment
        attrs["length"] = segment.length

        segment_first_coord_point = Point(segment.coords[0])
        segment_last_coord_point = Point(segment.coords[len(segment.coords) - 1])

        u_node_point = Point(G_modified.nodes[u]["x"], G_modified.nodes[u]["y"])
        v_node_point = Point(G_modified.nodes[v]["x"], G_modified.nodes[v]["y"])

        # First segment (of 2)
        if(i == 0):
            if(segment_first_coord_point == u_node_point or segment_last_coord_point == u_node_point):
                # create edge from u to new node
                # create in both directions to make sure it's bi-directional
                print(f"\tCreated first edge from {u} to {new_node_id}")
                G_modified.add_edge(u, new_node_id, **attrs)
                G_modified.add_edge(new_node_id, u, **attrs)
                make_v_next = True

            elif(segment_first_coord_point == v_node_point or segment_last_coord_point == v_node_point):
                G_modified.add_edge(v, new_node_id, **attrs)
                G_modified.add_edge(new_node_id, v, **attrs)
                print(f"\tCreated first edge from {v} to {new_node_id}")
                make_u_next = True
            else:
                # if the above logic falls through, find the node (u or v) that the first
                # segment coord is closest to, then create the edge from that node to the new node first
                u_to_segment_distance = shapely.distance(segment_first_coord_point, u_node_point)
                v_to_segment_distance = shapely.distance(segment_first_coord_point, v_node_point)

                print("\tSkipped first")

                if(u_to_segment_distance < v_to_segment_distance):
                    print(f"\tCreated first edge from {u} to {new_node_id}")
                    G_modified.add_edge(u, new_node_id, **attrs)
                    G_modified.add_edge(new_node_id, u, **attrs)
                    make_v_next = True
                else:
                    G_modified.add_edge(v, new_node_id, **attrs)
                    G_modified.add_edge(new_node_id, v, **attrs)
                    print(f"\tCreated first edge from {v} to {new_node_id}")
                    make_u_next = True

        # Second segment (of 2)
        elif(i == 1):
            if(make_v_next):
                # create edge from new node to v
                G_modified.add_edge(new_node_id, v, **attrs)
                G_modified.add_edge(v, new_node_id, **attrs)
                print(f"\tCreated second edge from {new_node_id} to {v}")
            elif(make_u_next):
                G_modified.add_edge(new_node_id, u, **attrs)
                G_modified.add_edge(u, new_node_id, **attrs)
                print(f"\tCreated second edge from {new_node_id} to {u}")
            else:
                print("\tSkipped second -------")
                print(f"\t\tU: {u}, V: {v}")
                print(f"\t\tNew Node: {new_node_id}")

	Created first edge from 1484783632 to 12871757001
	Created second edge from 12871757001 to 1794777143
	Created first edge from 5256999125 to 12871757002
	Created second edge from 12871757002 to 5256999127
	Created first edge from 5084858920 to 12871757003
	Created second edge from 12871757003 to 5084858913
	Created first edge from 5084844747 to 12871757004
	Created second edge from 12871757004 to 5084844750
	Created first edge from 12002096147 to 12871757005
	Created second edge from 12871757005 to 12002096148
	Created first edge from 5061087062 to 12871757006
	Created second edge from 12871757006 to 5061087063
	Created first edge from 10134631790 to 12871757007
	Created second edge from 12871757007 to 10134631787
	Created first edge from 4172469971 to 12871757008
	Created second edge from 12871757008 to 4172469980
	Created first edge from 12650954409 to 12871757009
	Created second edge from 12871757009 to 12650954408
	Created first edge from 1790320808 to 12871757010
	Created second 

In [40]:
# add time in minutes to traverse each edge in the graph
meters_per_minute = travel_speed * 1000 / 60  # km per hour to m per minute
for _, _, _, data in G_modified.edges(data=True, keys=True):
    data["time"] = data["length"] / meters_per_minute

In [45]:
# helper function for creating walksheds
def make_iso_polys(graph, origin, trip_times, uid, layer_name, edge_buff=25, node_buff=50, infill=False):
    isochrone_polys = []
    
    # normalize trip_times to always be a list
    if isinstance(trip_times, (int, float)):
        trip_times = [trip_times]
    
    for trip_time in trip_times:
        subgraph = nx.ego_graph(graph, origin, radius=trip_time, distance="time")

        node_points = [Point((data["x"], data["y"])) for node, data in subgraph.nodes(data=True)]
        nodes_gdf = gpd.GeoDataFrame({"id": list(subgraph.nodes)}, geometry=node_points)
        nodes_gdf = nodes_gdf.set_index("id")

        edge_lines = []
        for n_fr, n_to in subgraph.edges():
            f = nodes_gdf.loc[n_fr].geometry
            t = nodes_gdf.loc[n_to].geometry

            edge_data = graph.get_edge_data(n_fr, n_to)
            if edge_data:
                # Safely get the first edge’s geometry, or fallback to straight line
                first_edge = list(edge_data.values())[0]
                edge_geom = first_edge.get("geometry", LineString([f, t]))
            else:
                edge_geom = LineString([f, t])

            edge_lines.append(edge_geom)
            
            # edge_lookup = graph.get_edge_data(n_fr, n_to)[0].get("geometry", LineString([f, t]))
            # edge_lines.append(edge_lookup)

        print(edge_lines)

        n = nodes_gdf.buffer(node_buff).geometry
        e = gpd.GeoSeries(edge_lines).buffer(edge_buff).geometry
        all_gs = list(n) + list(e)
        new_iso = gpd.GeoSeries(all_gs).union_all()

        # if infill:
        #     if isinstance(new_iso, (MultiPolygon, Polygon)):
        #         new_iso = Polygon(new_iso.exterior)
                

        isochrone_polys.append(
        {
            'uid': uid,
            'layer_name': layer_name,
            'walk_time': trip_time,
            'geometry': new_iso
        })

        # convert to a pandas df
        iso_df = pd.DataFrame(isochrone_polys, columns=['uid', 'layer_name', 'walk_time', 'geometry'])

    return iso_df

In [46]:
# Set walk time for buffers, can also pass in list of values
walk_time = 15

# Process all stops
features = []

#temp_gdf =  gdf_nearest_points_copy[gdf_nearest_points_copy.uid == 1]
temp_gdf = gdf_nearest_points_copy

print(temp_gdf)

for idx, row in temp_gdf.iterrows():

    center_node = row['node_id']

    iso_polys = make_iso_polys(G_modified, center_node, walk_time, row.uid, row.layer_name, edge_buff=25, node_buff=0, infill=True)

    features.append(iso_polys)


# use concat with ignore index to remove duplicate column names and index from 0 to n-1
final_df = pd.concat(features, ignore_index=True)

# Create GeoDataFrame
iso_gdf = gpd.GeoDataFrame(final_df, crs=G.graph['crs'])

# Reproject to EPSG:4326 (WGS84 lat/lon)
iso_gdf = iso_gdf.to_crs("EPSG:4326")

print("outputting GeoJSON to 'walkshed_15min.geojson'")

# Export to GeoJSON
iso_gdf.to_file("data/walkshed_15min.geojson", driver="GeoJSON")

    uid      node_id          layer_name                        geometry
0     1  12871757001      grocery_stores  POINT (557770.652 4307184.786)
1     2  12871757002      grocery_stores  POINT (558576.482 4307409.481)
2     3  12871757003      grocery_stores  POINT (557601.769 4311461.242)
3     4  12871757004      grocery_stores  POINT (555574.696 4309995.877)
4     5  12871757005      grocery_stores  POINT (553509.133 4312134.229)
5     6  12871757006      grocery_stores  POINT (553409.863 4311822.635)
6     7  12871757007      grocery_stores  POINT (551863.449 4311573.097)
7     8  12871757008      grocery_stores  POINT (560989.887 4312011.068)
8     9  12871757009      grocery_stores  POINT (561103.563 4312344.704)
9    10  12871757010      grocery_stores  POINT (556407.139 4313272.372)
10   11  12871757011      grocery_stores  POINT (561651.153 4312616.015)
11   12  12871757012      grocery_stores  POINT (564596.269 4312847.052)
12   13  12871757013      grocery_stores  POINT (56

In [ ]:
# -- Below for testing --

# for u, v, data in G_modified.edges(data=True):
#     print(data)
#     break  # Just preview one

# G = ox.projection.project_graph(G)
# print(G.graph['crs'])


{'osmid': 18343332, 'highway': 'residential', 'name': 'Turtle Creek Lane', 'oneway': False, 'reversed': False, 'length': 191.83237423375417, 'geometry': <LINESTRING (-92.336 38.861, -92.336 38.861, -92.336 38.861, -92.336 38.86, ...>, 'time': 2.5577649897833887}
